In [1]:
import numpy as np
import pandas as pd
import folium
import webbrowser
import os
import math

from h3 import h3
from folium import Map

In [2]:
file_path = 'zip_lat_long.csv'

In [3]:
def read_data(file_path):
    df = pd.read_csv(file_path)  
    return df

In [4]:
def create_map(clusters, df):
    # Create the map object
    map = Map(tiles="cartodbpositron", 
          attr= '© <a href="http://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors © <a href="http://cartodb.com/attributions#basemaps">CartoDB</a>')

    # Convert the clusters dictionary items to polygons and add them to the map
    for cluster in clusters.values():
        points = cluster['geom']
        # points = [p[::-1] for p in points]
        tooltip = "{0} deliveries".format(cluster['count'])
        polygon = folium.vector_layers.Polygon(locations=points, tooltip=tooltip,
                                               fill=True, 
                                               color='#ff0000', 
                                               fill_color='#ff0000', 
                                               fill_opacity=0.4, weight=3, opacity=0.4)
        polygon.add_to(map)

    # Determine the map bounding box
    max_lat = df.Latitude.max()
    min_lat = df.Latitude.min()
    max_lon = df.Longitude.max()
    min_lon = df.Longitude.min()
    
    # Fit the map to the bounds
    map.fit_bounds([[min_lat, min_lon], [max_lat, max_lon]])
    
    return map


In [5]:
df_zip_codes = read_data(file_path)
df_zip_codes = df_zip_codes.rename(columns={"zip_lat": "Latitude", "zip_lon": "Longitude"})

In [6]:
df_zip_codes.head()

name   Latitude  Longitude
0  BD1  53.797379  -1.754058
1  BD2  53.815544  -1.736610
2  BD3  53.799762  -1.725094
3  BD4  53.771784  -1.705619
4  BD5  53.776589  -1.757621

In [19]:
h3_level = 7

In [20]:
def lat_lng_to_h3(row):
    return h3.geo_to_h3(row['Latitude'], row['Longitude'], h3_level)

In [21]:
df_zip_codes["h3"] = df_zip_codes.apply(lambda row: lat_lng_to_h3(row), axis=1)

In [22]:
df_zip_codes.head()

name   Latitude  Longitude               h3
0  BD1  53.797379  -1.754058  871942cceffffff
1  BD2  53.815544  -1.736610  871942cc1ffffff
2  BD3  53.799762  -1.725094  871942cceffffff
3  BD4  53.771784  -1.705619  871942cc8ffffff
4  BD5  53.776589  -1.757621  871942ccaffffff

In [23]:
deliveries = dict()

for index, row in df_zip_codes.iterrows():
    key = row['h3']
    if key in deliveries:
        deliveries[key]['count'] += 1
    else:
        deliveries[key] = {"count": 1,
                         "geom": h3.h3_to_geo_boundary(key)}

In [24]:
create_map(deliveries, df_zip_codes)